# wobbly_frog_53

## [wandb-wobbly_frog_53](https://wandb.ai/wako/matcha_tts_e/runs/kfr9xqqy?nw=nwuserwako)
- `GPU`: `NVIDIA GeForce RTX 4080`
- `Batch Size`: `16` (CPUs: `12`)
- **`gradient_clip_val`: `5.0` (Default)**
- `LR`: `1e-4`
- `normalize_orig`@ `text_mel_datamodule.py`
- `seed`: `2024`
- `precision`: `bf16-mixed`
- `max_epochs`: `1310`
- `MemoryCallBack` Added as hook.

## import

In [ ]:
%pwd

'/home/heiscold/matcha-tts/notebooks'

In [ ]:
import os
import sys

root_path= '/home/heiscold/matcha-tts/'
os.chdir(root_path)

import datetime as dt
from pathlib import Path
%matplotlib inline

import IPython.display as ipd
import numpy as np
import soundfile as sf
from tqdm.auto import tqdm

import numpy as np
# import pandas as pd

import torch
import torch.nn as nn

os.environ["CUDA_VISIBLE_DEVICES"]="0"
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
torch.cuda.is_available()

True

In [ ]:
# Matcha imports
from matcha.models.matcha_tts import MatchaTTS
from matcha.text import *
from matcha.utils.model import denormalize
from matcha.utils.utils import get_user_data_dir, intersperse
from matcha.utils.synthesize_utils import *

## Filepaths

In [ ]:
# HiFi-GAN
vocoder, vocoder_train_setup, denoiser = get_hifigan(device)

Using cache found in /home/heiscold/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub
/home/heiscold/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub/PyTorch/Classification/ConvNets/image_classification/models/common.py:13: UserWarning: pytorch_quantization module not found, quantization will not be available
  warnings.warn(
/home/heiscold/.cache/torch/hub/NVIDIA_DeepLearningExamples_torchhub/PyTorch/Classification/ConvNets/image_classification/models/efficientnet.py:17: UserWarning: pytorch_quantization module not found, quantization will not be available
  warnings.warn(


HiFi-GAN: Removing weight norm.
DownLoaded | NVIDIA's HiFi-GAN from torch hub | SR: 22050


In [ ]:
# Matcha-TTS
date = "2024-05-31_15-14-55"
# epoch_num = "1299"
# matcha_chkpt_path =  f"/home/heiscold/matcha-tts/logs/train/ljspeech/runs/{date}/checkpoints/checkpoint_epoch={epoch_num}.ckpt"
# matcha_chkpt_path =  f"/home/heiscold/matcha-tts/logs/train/ljspeech/runs/{date}/checkpoints/checkpoint_epoch=1299.ckpt"
matcha_chkpt_path =  f"/home/heiscold/matcha-tts/logs/train/ljspeech/runs/{date}/checkpoints/last.ckpt"

model = MatchaTTS.load_from_checkpoint(matcha_chkpt_path, map_location=device)
model = model.eval()

## Sentences

In [ ]:
# text = "I know that he is the world best professor."
text = "The Secret Service believed that it was very doubtful that any President would ride regularly in a vehicle with a fixed top, even though transparent."

## Number of ODE Solver steps
n_timesteps = 10

## Changes to the speaking rate
length_scale= 1.0

## Sampling temperature
temperature = 0.65

In [ ]:
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder, # = None,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
The Secret Service believed that it was very doubtful that any President would ride regularly in a vehicle with a fixed top, even though transparent.
-----------------------------------------------------
Phonetised text: 
_ð_ə_ _s_ˈ_i_ː_k_ɹ_ᵻ_t_ _s_ˈ_ɜ_ː_v_ɪ_s_ _b_ᵻ_l_ˈ_i_ː_v_d_ _ð_ˌ_ɐ_ɾ_ɪ_t_ _w_ʌ_z_ _v_ˈ_ɛ_ɹ_i_ _d_ˈ_a_ʊ_t_f_ə_l_ _ð_æ_t_ _ˌ_ɛ_n_i_ _p_ɹ_ˈ_ɛ_z_ɪ_d_ə_n_t_ _w_ʊ_d_ _ɹ_ˈ_a_ɪ_d_ _ɹ_ˈ_ɛ_ɡ_j_ʊ_l_ɚ_l_i_ _ɪ_n_ _ɐ_ _v_ˈ_i_ə_k_ə_l_ _w_ɪ_ð_ _ɐ_ _f_ˈ_ɪ_k_s_t_ _t_ˈ_ɑ_ː_p_,_ _ˈ_i_ː_v_ə_n_ _ð_ˌ_o_ʊ_ _t_ɹ_æ_n_s_p_ˈ_æ_ɹ_ə_n_t_._
-----------------------------------------------------
RTF:		0.020510
RTF Waveform:	0.030078


Not saving
Number of ODE steps: 10
Mean RTF:				0.020510 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.030078 ± 0.000000


## My name is Ro hoon and I am researching text-to-speech in my lab.

In [ ]:
text =  "My name is Ro hoon and I am researching text-to-speech in my lab."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
My name is Ro hoon and I am researching text-to-speech in my lab.
-----------------------------------------------------
Phonetised text: 
_m_a_ɪ_ _n_ˈ_e_ɪ_m_ _ɪ_z_ _ɹ_ˈ_o_ʊ_ _h_ˈ_u_ː_n_ _æ_n_d_ _ˈ_a_ɪ_ _æ_m_ _ɹ_ᵻ_s_ˈ_ɜ_ː_t_ʃ_ɪ_ŋ_ _t_ˈ_ɛ_k_s_t_t_ə_s_p_ˈ_i_ː_t_ʃ_ _ɪ_n_ _m_a_ɪ_ _l_ˈ_æ_b_._
-----------------------------------------------------
RTF:		0.012234
RTF Waveform:	0.023701


Not saving
Number of ODE steps: 10
Mean RTF:				0.012234 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.023701 ± 0.000000


## Hello, My name is John Wick and I am a professional killer.

In [ ]:
text = "Hello, My name is John Wick and I am a professional killer."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Hello, My name is John Wick and I am a professional killer.
-----------------------------------------------------
Phonetised text: 
_h_ə_l_ˈ_o_ʊ_,_ _m_a_ɪ_ _n_ˈ_e_ɪ_m_ _ɪ_z_ _d_ʒ_ˈ_ɑ_ː_n_ _w_ˈ_ɪ_k_ _æ_n_d_ _ˈ_a_ɪ_ _æ_m_ _ɐ_ _p_ɹ_ə_f_ˈ_ɛ_ʃ_ə_n_ə_l_ _k_ˈ_ɪ_l_ɚ_._
-----------------------------------------------------
RTF:		0.014439
RTF Waveform:	0.028027


Not saving
Number of ODE steps: 10
Mean RTF:				0.014439 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.028027 ± 0.000000


## I think there is something wrong with this model.

In [ ]:
text = "I think there is something wrong with this model."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
I think there is something wrong with this model.
-----------------------------------------------------
Phonetised text: 
_ˈ_a_ɪ_ _θ_ˈ_ɪ_ŋ_k_ _ð_ɛ_ɹ_ _ɪ_z_ _s_ˈ_ʌ_m_θ_ɪ_ŋ_ _ɹ_ˈ_ɔ_ŋ_ _w_ɪ_ð_ _ð_ɪ_s_ _m_ˈ_ɑ_ː_d_ə_l_._
-----------------------------------------------------
RTF:		0.020717
RTF Waveform:	0.039956


Not saving
Number of ODE steps: 10
Mean RTF:				0.020717 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.039956 ± 0.000000


## I think this model can synthesize only sentences that he learned.

In [ ]:
text = "I think this model can synthesize only sentences that he learned."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
I think this model can synthesize only sentences that he learned.
-----------------------------------------------------
Phonetised text: 
_ˈ_a_ɪ_ _θ_ˈ_ɪ_ŋ_k_ _ð_ɪ_s_ _m_ˈ_ɑ_ː_d_ə_l_ _k_æ_n_ _s_ˈ_ɪ_n_θ_ə_s_ˌ_a_ɪ_z_ _ˈ_o_ʊ_n_l_i_ _s_ˈ_ɛ_n_t_ə_n_s_ᵻ_z_ _ð_æ_t_ _h_i_ː_ _l_ˈ_ɜ_ː_n_d_._
-----------------------------------------------------
RTF:		0.013418
RTF Waveform:	0.025673


Not saving
Number of ODE steps: 10
Mean RTF:				0.013418 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.025673 ± 0.000000


## If there is a hope that you can replace with something better.

In [ ]:
text = "If there is a hope that you can replace with something better."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
If there is a hope that you can replace with something better.
-----------------------------------------------------
Phonetised text: 
_ɪ_f_ _ð_ɛ_ɹ_ _ɪ_z_ _ɐ_ _h_ˈ_o_ʊ_p_ _ð_æ_t_ _j_u_ː_ _k_æ_n_ _ɹ_ᵻ_p_l_ˈ_e_ɪ_s_ _w_ɪ_ð_ _s_ˈ_ʌ_m_θ_ɪ_ŋ_ _b_ˈ_ɛ_ɾ_ɚ_._
-----------------------------------------------------
RTF:		0.014730
RTF Waveform:	0.028263


Not saving
Number of ODE steps: 10
Mean RTF:				0.014730 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.028263 ± 0.000000


## The day you started to disappear was doom's day for me.

In [ ]:
text = "The day you started to disappear was doom's day for me"
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
The day you started to disappear was doom's day for me
-----------------------------------------------------
Phonetised text: 
_ð_ə_ _d_ˈ_e_ɪ_ _j_u_ː_ _s_t_ˈ_ɑ_ː_ɹ_ɾ_ᵻ_d_ _t_ə_ _d_ˌ_ɪ_s_ɐ_p_ˈ_ɪ_ɹ_ _w_ʌ_z_ _d_ˈ_u_ː_m_z_ _d_ˈ_e_ɪ_ _f_ɔ_ː_ɹ_ _m_ˌ_i_ː_
-----------------------------------------------------
RTF:		0.014061
RTF Waveform:	0.027249


Not saving
Number of ODE steps: 10
Mean RTF:				0.014061 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.027249 ± 0.000000


## Speech conveys more information than text, as the same word can be uttered in various voices to convey diverse information.

In [ ]:
text = "Speech conveys more information than text, as the same word can be uttered in various voices to convey diverse information."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Speech conveys more information than text, as the same word can be uttered in various voices to convey diverse information.
-----------------------------------------------------
Phonetised text: 
_s_p_ˈ_i_ː_t_ʃ_ _k_ə_n_v_ˈ_e_ɪ_z_ _m_ˈ_o_ː_ɹ_ _ˌ_ɪ_n_f_ɚ_m_ˈ_e_ɪ_ʃ_ə_n_ _ð_ɐ_n_ _t_ˈ_ɛ_k_s_t_,_ _æ_z_ _ð_ə_ _s_ˈ_e_ɪ_m_ _w_ˈ_ɜ_ː_d_ _k_æ_n_ _b_i_ː_ _ˈ_ʌ_ɾ_ɚ_d_ _ɪ_n_ _v_ˈ_ɛ_ɹ_i_ə_s_ _v_ˈ_ɔ_ɪ_s_ᵻ_z_ _t_ə_ _k_ə_n_v_ˈ_e_ɪ_ _d_a_ɪ_v_ˈ_ɜ_ː_s_ _ˌ_ɪ_n_f_ɚ_m_ˈ_e_ɪ_ʃ_ə_n_._
-----------------------------------------------------
RTF:		0.007494
RTF Waveform:	0.014436


Not saving
Number of ODE steps: 10
Mean RTF:				0.007494 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.014436 ± 0.000000


## The committee does not seem to have yet understood that Newgate could be only and properly replaced.

In [ ]:
text = "The committee does not seem to have yet understood that Newgate could be only and properly replaced."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
The committee does not seem to have yet understood that Newgate could be only and properly replaced.
-----------------------------------------------------
Phonetised text: 
_ð_ə_ _k_ə_m_ˈ_ɪ_ɾ_i_ _d_ʌ_z_n_ˌ_ɑ_ː_t_ _s_ˈ_i_ː_m_ _t_ə_ _h_æ_v_ _j_ˈ_ɛ_t_ _ˌ_ʌ_n_d_ɚ_s_t_ˈ_ʊ_d_ _ð_æ_t_ _n_ˈ_u_ː_ɡ_e_ɪ_t_ _k_ʊ_d_ _b_i_ː_ _ˈ_o_ʊ_n_l_i_ _æ_n_d_ _p_ɹ_ˈ_ɑ_ː_p_ɚ_l_i_ _ɹ_ᵻ_p_l_ˈ_e_ɪ_s_t_._
-----------------------------------------------------
RTF:		0.009844
RTF Waveform:	0.019066


Not saving
Number of ODE steps: 10
Mean RTF:				0.009844 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.019066 ± 0.000000


## From defection to return to Fort Worth.

In [ ]:
text = "From defection to return to Fort Worth."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
From defection to return to Fort Worth.
-----------------------------------------------------
Phonetised text: 
_f_ɹ_ʌ_m_ _d_ᵻ_f_ˈ_ɛ_k_ʃ_ə_n_ _t_ə_ _ɹ_ᵻ_t_ˈ_ɜ_ː_n_ _t_ə_ _f_ˈ_ɔ_ː_ɹ_t_ _w_ˈ_ɜ_ː_θ_._
-----------------------------------------------------
RTF:		0.018691
RTF Waveform:	0.036234


Not saving
Number of ODE steps: 10
Mean RTF:				0.018691 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.036234 ± 0.000000


## Although the strain lasted fourteen days, he showed no signs of exhaustion, either physical or mental.

In [ ]:
text = "Although the strain lasted fourteen days, he showed no signs of exhaustion, either physical or mental."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Although the strain lasted fourteen days, he showed no signs of exhaustion, either physical or mental.
-----------------------------------------------------
Phonetised text: 
_ɔ_ː_l_ð_ˈ_o_ʊ_ _ð_ə_ _s_t_ɹ_ˈ_e_ɪ_n_ _l_ˈ_æ_s_t_ᵻ_d_ _f_ˈ_o_ː_ɹ_t_i_ː_n_ _d_ˈ_e_ɪ_z_,_ _h_i_ː_ _ʃ_ˈ_o_ʊ_d_ _n_ˈ_o_ʊ_ _s_ˈ_a_ɪ_n_z_ _ʌ_v_ _ɛ_ɡ_z_ˈ_ɔ_ː_s_t_ʃ_ə_n_,_ _ˈ_i_ː_ð_ɚ_ _f_ˈ_ɪ_z_ɪ_k_ə_l_ _ɔ_ː_ɹ_ _m_ˈ_ɛ_n_t_ə_l_._
-----------------------------------------------------
RTF:		0.009255
RTF Waveform:	0.017529


Not saving
Number of ODE steps: 10
Mean RTF:				0.009255 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.017529 ± 0.000000


## She knew that the hard thing to do was the thing that had to be done.

In [ ]:
text = "She knew that the hard thing to do was the thing that had to be done."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
She knew that the hard thing to do was the thing that had to be done.
-----------------------------------------------------
Phonetised text: 
_ʃ_i_ː_ _n_ˈ_u_ː_ _ð_æ_t_ð_ə_ _h_ˈ_ɑ_ː_ɹ_d_ _θ_ˈ_ɪ_ŋ_ _t_ə_ _d_ˈ_u_ː_ _w_ʌ_z_ð_ə_ _θ_ˈ_ɪ_ŋ_ _ð_æ_t_ _h_æ_d_t_ə_ _b_i_ː_ _d_ˈ_ʌ_n_._
-----------------------------------------------------
RTF:		0.011647
RTF Waveform:	0.024798


Not saving
Number of ODE steps: 10
Mean RTF:				0.011647 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.024798 ± 0.000000


## And by hard, It means impossible.

In [ ]:
text = "And by hard, It means impossible."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
And by hard, It means impossible.
-----------------------------------------------------
Phonetised text: 
_æ_n_d_ _b_a_ɪ_ _h_ˈ_ɑ_ː_ɹ_d_,_ _ɪ_t_ _m_ˈ_i_ː_n_z_ _ɪ_m_p_ˈ_ɑ_ː_s_ᵻ_b_ə_l_._
-----------------------------------------------------
RTF:		0.024185
RTF Waveform:	0.045781


Not saving
Number of ODE steps: 10
Mean RTF:				0.024185 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.045781 ± 0.000000


## You Just Choose Your Burden.

In [ ]:
text = "You Just Choose Your Burden."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
You Just Choose Your Burden.
-----------------------------------------------------
Phonetised text: 
_j_u_ː_ _d_ʒ_ˈ_ʌ_s_t_ _t_ʃ_ˈ_u_ː_z_ _j_ʊ_ɹ_ _b_ˈ_ɜ_ː_d_ə_n_._
-----------------------------------------------------
RTF:		0.025117
RTF Waveform:	0.048209


Not saving
Number of ODE steps: 10
Mean RTF:				0.025117 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.048209 ± 0.000000


## Was used for debtors arrested for the lowest sums within twelve miles of the palace of Whitehall.

In [ ]:
text = "Was used for debtors arrested for the lowest sums within twelve miles of the palace of Whitehall."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Was used for debtors arrested for the lowest sums within twelve miles of the palace of Whitehall.
-----------------------------------------------------
Phonetised text: 
_w_ʌ_z_ _j_ˈ_u_ː_z_d_ _f_ɔ_ː_ɹ_ _d_ˈ_ɛ_ɾ_ɚ_z_ _ɚ_ɹ_ˈ_ɛ_s_t_ᵻ_d_ _f_ɚ_ð_ə_ _l_ˈ_o_ʊ_ɪ_s_t_ _s_ˈ_ʌ_m_z_ _w_ɪ_ð_ˌ_ɪ_n_ _t_w_ˈ_ɛ_l_v_ _m_ˈ_a_ɪ_l_z_ _ʌ_v_ð_ə_ _p_ˈ_æ_l_ɪ_s_ _ʌ_v_ _w_ˈ_a_ɪ_t_h_ɔ_ː_l_._
-----------------------------------------------------
RTF:		0.011233
RTF Waveform:	0.023227


Not saving
Number of ODE steps: 10
Mean RTF:				0.011233 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.023227 ± 0.000000


##  Were the leaders in this luckless change, though our own Baskerville, who was at work some years before them, went much on the same lines.

In [ ]:
text = "Were the leaders in this luckless change, though our own Baskerville, who was at work some years before them, went much on the same lines."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Were the leaders in this luckless change, though our own Baskerville, who was at work some years before them, went much on the same lines.
-----------------------------------------------------
Phonetised text: 
_w_ɜ_ː_ _ð_ə_ _l_ˈ_i_ː_d_ɚ_z_ _ɪ_n_ _ð_ɪ_s_ _l_ˈ_ʌ_k_l_ə_s_ _t_ʃ_ˈ_e_ɪ_n_d_ʒ_,_ _ð_ˌ_o_ʊ_ _ˌ_a_ʊ_ɚ_ɹ_ _ˈ_o_ʊ_n_ _b_ˈ_æ_s_k_ɚ_v_ˌ_ɪ_l_,_ _h_ˌ_u_ː_ _w_ʌ_z_ _æ_t_ _w_ˈ_ɜ_ː_k_ _s_ˌ_ʌ_m_ _j_ˈ_ɪ_ɹ_z_ _b_ᵻ_f_ˈ_o_ː_ɹ_ _ð_ˌ_ɛ_m_,_ _w_ɛ_n_t_ _m_ˈ_ʌ_t_ʃ_ _ɔ_n_ð_ə_ _s_ˈ_e_ɪ_m_ _l_ˈ_a_ɪ_n_z_._
-----------------------------------------------------
RTF:		0.006627
RTF Waveform:	0.013191


Not saving
Number of ODE steps: 10
Mean RTF:				0.006627 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.013191 ± 0.000000


## Notably as when numbers filled Newgate in anticipation of Lord Redesdale’s bill for insolvent debtors.

In [ ]:
text = "Notably as when numbers filled Newgate in anticipation of Lord Redesdale’s bill for insolvent debtors."
output, rtfs, rtfs_w = synthesis_to_speech(
    texts = [text],
    model = model,
    vocoder = vocoder,
    denoiser = denoiser,
    denoising_strength = 0.00025,
    spks = None,
    n_timesteps = n_timesteps,
    length_scale = length_scale,
    temperature = temperature,
    save_wav = False,
    OUTPUT_FOLDER = './',
    device = device)

print(f"Number of ODE steps: {n_timesteps}")
print(f"Mean RTF:\t\t\t\t{np.mean(rtfs):.6f} ± {np.std(rtfs):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")
print(f"Mean RTF Waveform (incl. vocoder):\t{np.mean(rtfs_w):.6f} ± {np.std(rtfs_w):.6f}")

  0%|          | 0/1 [00:00<?, ?it/s]

Input text: 
Notably as when numbers filled Newgate in anticipation of Lord Redesdale’s bill for insolvent debtors.
-----------------------------------------------------
Phonetised text: 
_n_ˈ_o_ʊ_ɾ_ə_b_l_i_ _æ_z_ _w_ɛ_n_ _n_ˈ_ʌ_m_b_ɚ_z_ _f_ˈ_ɪ_l_d_ _n_ˈ_u_ː_ɡ_e_ɪ_t_ _ɪ_n_ _æ_n_t_ˈ_ɪ_s_ɪ_p_ˈ_e_ɪ_ʃ_ə_n_ _ʌ_v_ _l_ˈ_ɔ_ː_ɹ_d_ _ɹ_ˌ_i_ː_d_ᵻ_s_d_ˈ_e_ɪ_l_z_ _b_ˈ_ɪ_l_ _f_ɔ_ː_ɹ_ _ɪ_n_s_ˈ_ɑ_ː_l_v_ə_n_t_ _d_ˈ_ɛ_ɾ_ɚ_z_._
-----------------------------------------------------
RTF:		0.008159
RTF Waveform:	0.016048


Not saving
Number of ODE steps: 10
Mean RTF:				0.008159 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.016048 ± 0.000000
Mean RTF Waveform (incl. vocoder):	0.016048 ± 0.000000
